In [ ]:
/************************************************************************
 * Last Run Date: 01 April 2017	            							*
 * Program Name: panders2_hw10_prog.sas									*
 * Program Location: C:/Users/Philip/Schools/TAMU/STAT_657/				*
 *				SASUniversityEdition/myfolders/homework/git_hw/hw_10/sasprogs/	* 
 * Creation Date: 01 April 2017											*
 * Author: Philip Anderson												*
 * Purpose: Meeting objectives for Assignment 08						*
 * Inputs: orion folder         *
 * Output: panders2_hw10_output.pdf															*
 * Modification History: *
 * Execution Instructions: N/A - run as-is												*
*/**********************************************************************;


In [4]:
/* 
Question 3 (Questions 1 + 2 not documented here) - set a system option
 that writes macro variables to the log as they are resolved, and another option
 that writes to the SAS log the text that is generated by macro execution
*/
options symbolgen mprint;

/* below is from question 5 */
%let hw_num = 10;


In [13]:
/* 
Question 4 - set up your SAS session so that it can find the autocall macro program saved in step 1 
*/
libname macros '/folders/myfolders/macros' access=readonly;
options mautosource sasautos=macros;


In [11]:
/* 
Question 5 - Set up an "A&M" folder at the same level as "macros"
create a fileref path to it, and make the hw number a macro variable
use a function to mask the macro functionality of the ampersand in A&M
*/

filename pdf_out "/folders/myfolders/%nrstr(A&M)/panders2_hw&hw_num._output.pdf";



In [16]:
/* Question 6 - run the colormac function in your program */

%donate();



In [21]:

/* Question 8 - use the catalog procedure to list macros stored in the work library */

proc catalog cat=work.SASMAC1;
    contents;
run;


In [24]:
/************************************************************************
 Description: Assignment 10
 Philip Anderson
 Created: 01 April 2017
*/**********************************************************************;

/* Copying the donations code from Step 4 of Assignment 09 */

libname orion "/folders/myfolders/orion_dat/sasdata" access=readonly;

%macro donate(outlib, gender, startdt, enddt); 
** Convert the status to proper case; 
%let gender=%sysfunc(propcase(&gender)); 

proc sql;    
create table &outlib..&gender%substr(&startdt,6) as    
select 
c.employee_id 'ID'
, employee_name 'Name'
, salary format=dollar8.
, qtr1, qtr2, qtr3, qtr4
, sum(qtr1, qtr2, qtr3, qtr4) as tot_donation 'Ann. Donation'    
from 
(
    select 
    a.employee_id
    , employee_name
    , salary        
    from orion.employee_payroll a
    , orion.employee_addresses b        
    where a.employee_id=b.employee_id 
    and employee_term_date is missing 
    and (employee_hire_date between "&startdt"d and "&enddt"d) 
    and employee_gender = "%substr(&gender,1,1)"
) as c    

left join    
orion.employee_donations as d    
on c.employee_id=d.employee_id
;

title "Donations of &gender Employees Hired between &startdt and &enddt"; 
footnote "&syslast";    

select 
*    
from 
&outlib..&gender%substr(&startdt,6);    

/* It would be acceptable to use &syslast on the from statement above. */ 
quit;

/* Housekeeping */ title;
footnote;

%mend donate;



In [25]:
%donate(work, female, 01Jan1996, 31Dec2005)

In [27]:
proc sql;
select 
*
from
dictionary.catalogs;
quit;

In [41]:
/* Use a data step to create a new table called f9605, based on the Female1996 data set created above */

data f9605;
set Female1996 (keep=employee_id employee_name salary);
    if _n_=1 then do;
        call symputx('emp_id', employee_id);
        call symputx('sal', salary);
    end;

    if salary > symget(sal) then do;
        sal_great = 1;
    end;
    
    else sal_great=0;
    
run;

*%put &emp_id. &sal. &emp_id_b. &sal_b.;

proc print data=f9605; run;